In [1]:
import folium
import pickle
from osm_flex.config import *
import geojson
import sys
from shapely.geometry import shape
from shapely.geometry import Polygon, MultiPolygon

sys.path.append(r'C:\repos\ra2ce_multi_network') # path to the package
from simplify_rail import _unified_buffer_tracks, _remove_small_holes, _triangulate_polygon

C:\Users\asgarpou\AppData\Local\miniconda3\envs\ra2ce_multi_network_env\lib\site-packages\geopandas\_compat.py:124: UserWarning: The Shapely GEOS version (3.11.2-CAPI-1.17.2) is incompatible with the GEOS version PyGEOS was compiled with (3.10.4-CAPI-1.16.2). Conversions between both will be slow.
  warnings.warn(


In [2]:
## Defining ini variables
root_folder = Path(
    # r'C:\Users\asgarpou\OneDrive - Stichting Deltares\Documents\Projects\SITO_Netwerk to system\content\input_data\pbf'
    r'C:\Users\asgarpou\osm'
)

# area-related
study_area_suffix = '_test' # small case study area
clip_output_name = f'study_area{study_area_suffix}'

# Load complex and merged networks
complex_network_file = root_folder.joinpath(f'networks/complex_rail_network_{clip_output_name}.geojson')
merged_network_file = root_folder.joinpath(f'networks/merged_rail_network_{clip_output_name}.geojson')

with open(complex_network_file, 'rb') as handle:
    complex_rail_network = pickle.load(handle)

with open(merged_network_file, 'rb') as handle:
    merged_rail_network = pickle.load(handle)

In [3]:
# Show a railway networks with possible terminal nodes
m = merged_rail_network.edges.explore(tiles="CartoDB positron")

In [4]:
## Simplify tracks steps
# make a clean unified buffer polygon
unified_buffer = _unified_buffer_tracks(merged_rail_network, 0.01) # buffer range is in km
m = unified_buffer.explore(tiles="CartoDB positron", m=m)

clean_unified_buffer = _remove_small_holes(unified_buffer, 0.01) # hole area is set to 10k km2 (according to the literature)
m = clean_unified_buffer.explore(tiles="CartoDB positron", m=m)


C:\repos\ra2ce_multi_network\ra2ce_multi_network\simplify_rail.py:478: UserWarning: Geometry is in a geographic CRS. Results from 'buffer' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  buffered_data = net.edges.geometry.to_crs('EPSG:4326').buffer(buffer_distance_deg)


In [5]:
# Triangulate the buffered plygon
triangles = _triangulate_polygon(clean_unified_buffer)